# Experiments with mapping EHRI and HGC camps datasets

In [5]:
import pandas as pd
import geopandas as gp

import numpy as np

import folium

For simplification, let's first make use of pre-generated list of EHRI camps:
https://portal.ehri-project.eu/api/datasets/rioyBacGZL

In [6]:
ehri_camps_url = 'https://portal.ehri-project.eu/api/datasets/rioyBacGZL?format=csv'
campsdf = pd.read_csv(ehri_camps_url, names=['ehri_id', 'name', 'lat', 'lon', 'relations'], header=None)
campsdf.head()

ehri_id                             name        lat        lon  \
0  ehri_camps-3001  Vivikonna OT concentration camp  59.338000  27.674600   
1  ehri_camps-1617     Septfonds concentration camp  44.180249   1.619641   
2  ehri_camps-2508      Masseube concentration camp  43.430806   0.579694   
3  ehri_camps-2062       Missler concentration camp  53.093399   8.802200   
4  ehri_camps-2233        Zittau concentration camp  50.900001  14.833299   

   relations  
0          2  
1          3  
2          1  
3          1  
4          1

In [7]:
campsgdf = gp.GeoDataFrame(
    campsdf, geometry=gp.points_from_xy(campsdf.lon, campsdf.lat))
campsgdf.head()

ehri_id                             name        lat        lon  \
0  ehri_camps-3001  Vivikonna OT concentration camp  59.338000  27.674600   
1  ehri_camps-1617     Septfonds concentration camp  44.180249   1.619641   
2  ehri_camps-2508      Masseube concentration camp  43.430806   0.579694   
3  ehri_camps-2062       Missler concentration camp  53.093399   8.802200   
4  ehri_camps-2233        Zittau concentration camp  50.900001  14.833299   

   relations                   geometry  
0          2  POINT (27.67460 59.33800)  
1          3   POINT (1.61964 44.18025)  
2          1   POINT (0.57969 43.43081)  
3          1   POINT (8.80220 53.09340)  
4          1  POINT (14.83330 50.90000)

The pre-generated table used above, unfortuntely, doesn't inlude camps without links. Below we add the full EHRI camps data set. The CSV file has been created from the RDF file downloaded from the EHRI Portal (https://portal.ehri-project.eu/vocabularies/ehri_camps/export?format=RDF%2FXML), using a XSLT stylesheet.

In [8]:
campsdf2 = pd.read_csv('EHRI_camps.csv', names=['EHRI_URI', 'name', 'altname', 'lon', 'lat', 'broader'], header=None)
campsdf2.head()

EHRI_URI  \
0    "http://data.ehri-project.eu/vocabularies/eh...   
1    "http://data.ehri-project.eu/vocabularies/eh...   
2    "http://data.ehri-project.eu/vocabularies/eh...   
3    "http://data.ehri-project.eu/vocabularies/eh...   
4    "http://data.ehri-project.eu/vocabularies/eh...   

                                                name  \
0                       Ciechanów concentration camp   
1                 Most na Ostrove concentration camp   
2                     Johannsdorf concentration camp   
3                         Namslau concentration camp   
4  Wien-Ebergassing (Graf Marenzi) concentration ...   

                                    altname        lon        lat  \
0               Zichenau concentration camp  20.616666  52.883333   
1                                       NaN  17.268000  48.142000   
2  Zwangsarbeitslager für Juden Johannsdorf        NaN        NaN   
3                                       NaN        NaN        NaN   
4                                       NaN        NaN        NaN   

                                             broader  
0                                                NaN  
1                                                NaN  
2                                                NaN  
3  http://data.ehri-project.eu/vocabularies/ehri-...  
4                                                NaN

Drop lines without coordinates.

In [9]:
campsdf2 = campsdf2.dropna(subset=['lat', 'lon'])

Create empty map useing folium.

In [10]:
# Stamen Toner
map = folium.Map(location=[np.average(campsdf['lat']), np.average(campsdf['lon'])], tiles='Cartodb Positron', zoom_start = 6)
map

EHRI Camp data (incl. those without links)

In [11]:
for index, row in campsdf2.iterrows():
    folium.Marker(location=[row['lat'],row['lon']], icon=folium.Icon(color='red', icon='exclamation', prefix='fa'), 
        popup=row['name']).add_to(map)
map

Holocaust Geographies Collaborative camps dataset

In [12]:
hg_camps = "https://holocaustgeographies.org/sites/default/files/2020-09/SSCampDataset.zip"

hg_camps_gdf = gp.read_file(hg_camps)
hg_camps_gdf.head()

ID  MHG_ID                 SUBCAMP       MAIN  WOMEN  MEN  GENDER  \
0  01-0009-0   502.0                 Altdorf  Auschwitz    0.0  0.0     0.0   
1  01-0013-0   503.0               Althammer  Auschwitz    0.0  0.0     0.0   
2  01-0032-3   504.0             Auschwitz I  Auschwitz    2.0  1.0     3.0   
3  01-0033-3   505.0   Auschwitz II Birkenau  Auschwitz    2.0  1.0     3.0   
4  01-0034-0   506.0  Auschwitz III Monowitz  Auschwitz    0.0  0.0     0.0   

                                               FIRMS YYYY_OPEN MM_OPEN  ...  \
0                   Pless Forestry Management Office        42      10  ...   
1                                               None        44      09  ...   
2  IG Farben, Herman Goring Works, German Equipme...        40      06  ...   
3                                               None        43      11  ...   
4                                               None        41      04  ...   

  HOW_FOUND SHARE_LOC        LAT       LONG                         NATIONS  \
0      None         0  49.983299  18.916700                            None   
1      None         0  51.400001  17.466699  France, Poland, Hungary, Dutch   
2      None         0  50.026199  19.204099                 All over Europe   
3      None         0  50.037100  19.175200                 All over Europe   
4      None         0  50.031101  19.291500                            None   

                                    ENCY_REF  \
0     Encyclopedia of Camps, Volume 1 pg 224   
1     Encyclopedia of Camps, Volume 1 pg 224   
2     Encyclopedia of Camps, Volume 1 pg 204   
3  Encyclopedia of Camps and Ghettos, p. 209   
4     Encyclopedia of Camps, Volume 1 pg 215   

                                               LABOR  \
0  Forestry detail located in the basement of a h...   
1  Prisoners contructed the Walter thermal power ...   
2  Inmates worked in administrative, service, and...   
3  Extermination camp, prisoners built camp, most...   
4  Prisoners built and worked in an IG Farben fac...   

                                          EDIT_NOTES             FIRMABBREV  \
0                                               None                   None   
1                                               None                   None   
2                                               None  IG Farben, RWHG, DESt   
3                      BB added N_FIRM data 7/3/2012                   None   
4  AK added Open YYYY and Open MM and Date_Evac_T...                   None   

                    geometry  
0  POINT (18.91670 49.98330)  
1  POINT (17.46670 51.40000)  
2  POINT (19.20410 50.02620)  
3  POINT (19.17520 50.03710)  
4  POINT (19.29150 50.03110)  

[5 rows x 32 columns]

Join both datasets...

In [32]:
m = folium.Map(location=[np.average(campsdf['lat']), np.average(campsdf['lon'])], tiles='Cartodb Positron', zoom_start = 6)
folium.GeoJson(data=hg_camps_gdf["geometry"]).add_to(m)
# tooltip=folium.features.GeoJsonTooltip(fields=['MAIN', 'SUBCAMP'], localize=True)

for index, row in campsdf2.iterrows():
    folium.Marker(location=[row['lat'],row['lon']], icon=folium.Icon(color='red', icon='map-marker', prefix='fa'), rotationAngle=45, popup=row['name']).add_to(m)
#    folium.Marker(location=[row['lat'],row['lon']], icon_size=(8, 12), icon_color='red', popup=row['name']).add_to(m)
m